# RSI Scalping Strategy 1min

In [49]:
import pandas as pd
stdf = pd.read_csv("EURUSD_Candlestick_1_M_ASK_05.02.2019-05.02.2022.csv")
stdf.tail()

Local time     Open     High      Low    Close  \
1578355  05.02.2022 01:55:00.000 GMT+0200  1.14517  1.14517  1.14517  1.14517   
1578356  05.02.2022 01:56:00.000 GMT+0200  1.14517  1.14517  1.14517  1.14517   
1578357  05.02.2022 01:57:00.000 GMT+0200  1.14517  1.14517  1.14517  1.14517   
1578358  05.02.2022 01:58:00.000 GMT+0200  1.14517  1.14517  1.14517  1.14517   
1578359  05.02.2022 01:59:00.000 GMT+0200  1.14517  1.14517  1.14517  1.14517   

         Volume  
1578355     0.0  
1578356     0.0  
1578357     0.0  
1578358     0.0  
1578359     0.0

In [28]:
df=stdf[0:30000].copy()
df=df[df['Volume']!=0]
df.isna().sum()
df.reset_index(drop=True, inplace=True)
df.tail()

Local time     Open     High      Low    Close  \
21348  25.02.2019 19:55:00.000 GMT+0200  1.13455  1.13455  1.13445  1.13446   
21349  25.02.2019 19:56:00.000 GMT+0200  1.13446  1.13453  1.13446  1.13447   
21350  25.02.2019 19:57:00.000 GMT+0200  1.13448  1.13460  1.13448  1.13459   
21351  25.02.2019 19:58:00.000 GMT+0200  1.13459  1.13495  1.13458  1.13476   
21352  25.02.2019 19:59:00.000 GMT+0200  1.13477  1.13485  1.13473  1.13480   

       Volume  
21348  115.24  
21349  113.17  
21350  244.30  
21351  481.00  
21352  363.09

In [29]:
import pandas_ta as ta
df["EMA200"] = ta.ema(df.Close, length=200)
df["RSI"] = ta.rsi(df.Close, length=3)
df['ATR']= df.ta.atr()

In [30]:
df.tail()

Local time     Open     High      Low    Close  \
21348  25.02.2019 19:55:00.000 GMT+0200  1.13455  1.13455  1.13445  1.13446   
21349  25.02.2019 19:56:00.000 GMT+0200  1.13446  1.13453  1.13446  1.13447   
21350  25.02.2019 19:57:00.000 GMT+0200  1.13448  1.13460  1.13448  1.13459   
21351  25.02.2019 19:58:00.000 GMT+0200  1.13459  1.13495  1.13458  1.13476   
21352  25.02.2019 19:59:00.000 GMT+0200  1.13477  1.13485  1.13473  1.13480   

       Volume    EMA200        RSI       ATR  
21348  115.24  1.134779  14.501000  0.000159  
21349  113.17  1.134775  20.129751  0.000153  
21350  244.30  1.134774  63.446348  0.000151  
21351  481.00  1.134773  83.017782  0.000167  
21352  363.09  1.134774  85.716873  0.000163

## EMA Signal

In [31]:
emasignal = [0]*len(df)
backcandles = 30

for row in range(backcandles-1, len(df)):
    upt = 1
    dnt = 1
    for i in range(row-backcandles, row+1):
        if df.High[row]>=df.EMA200[row]:
            dnt=0
        if df.Low[row]<=df.EMA200[row]:
            upt=0
    if upt==1 and dnt==1:
        #print("!!!!! check trend loop !!!!")
        emasignal[row]=3
    elif upt==1:
        emasignal[row]=2
    elif dnt==1:
        emasignal[row]=1

df['EMAsignal'] = emasignal

## Total signal

In [32]:
TotSignal = [0] * len(df)
for row in range(0, len(df)):
    TotSignal[row] = 0
    if df.EMAsignal[row]==1 and df.RSI[row]>=90:
        TotSignal[row]=1
    if df.EMAsignal[row]==2 and df.RSI[row]<=10:
        TotSignal[row]=2

df['TotSignal']=TotSignal

In [33]:
df.tail()

Local time     Open     High      Low    Close  \
21348  25.02.2019 19:55:00.000 GMT+0200  1.13455  1.13455  1.13445  1.13446   
21349  25.02.2019 19:56:00.000 GMT+0200  1.13446  1.13453  1.13446  1.13447   
21350  25.02.2019 19:57:00.000 GMT+0200  1.13448  1.13460  1.13448  1.13459   
21351  25.02.2019 19:58:00.000 GMT+0200  1.13459  1.13495  1.13458  1.13476   
21352  25.02.2019 19:59:00.000 GMT+0200  1.13477  1.13485  1.13473  1.13480   

       Volume    EMA200        RSI       ATR  EMAsignal  TotSignal  
21348  115.24  1.134779  14.501000  0.000159          1          0  
21349  113.17  1.134775  20.129751  0.000153          1          0  
21350  244.30  1.134774  63.446348  0.000151          1          0  
21351  481.00  1.134773  83.017782  0.000167          0          0  
21352  363.09  1.134774  85.716873  0.000163          0          0

In [34]:
df.dropna(inplace=True)
df.reset_index(drop=True, inplace=True)

## Visualizing signals on chart

In [35]:
import numpy as np
def pointpos(x):
    if x['TotSignal']==1:
        return x['High']+1e-3
    elif x['TotSignal']==2:
        return x['Low']-1e-3
    else:
        return np.nan

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

In [36]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime

endid = 1000
startid = 0
dfpl = df[startid:endid]

fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),
                go.Scatter(x=dfpl.index, y=dfpl.EMA200, line=dict(color='red', width=1), name="EMA200")])

fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                marker=dict(size=5, color="MediumPurple"),
                name="Signal")
fig.show()

## Backtesting Strategy

In [37]:
dfpl = df[:]

def SIGNAL():
    return dfpl.TotSignal

In [47]:
from backtesting import Strategy
class MyStrat(Strategy):
    initsize = 0.2
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        
        #if(self.signal1>0 and len(self.trades)==0 and len(self.closed_trades)>0 and self.closed_trades[-1].pl < 0):
        #    self.mysize=self.mysize*2
        #elif len(self.closed_trades)>0 and self.closed_trades[-1].pl > 0:
        #    self.mysize=self.initsize

        if self.signal1==2 and len(self.trades)==0:   
            sl1 = self.data.Close[-1] - 45e-4
            tp1 = self.data.Close[-1] + 45e-4 #45
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.signal1==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + 45e-4
            tp1 = self.data.Close[-1] - 45e-4 #45
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

In [48]:
from backtesting import Backtest

bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.00)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21153.0
Duration                              21153.0
Exposure Time [%]                   97.069112
Equity Final [$]                    106.89019
Equity Peak [$]                     115.57226
Return [%]                            6.89019
Buy & Hold Return [%]               -0.773838
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -12.204209
Avg. Drawdown [%]                    -0.47102
Max. Drawdown Duration                13504.0
Avg. Drawdown Duration             183.265487
# Trades                                 11.0
Win Rate [%]                        54.545455
Best Trade [%]                       0.398442
Worst Trade [%]                     -0.399805
Avg. Trade [%]                    

In [40]:
bt.plot(show_legend=False)

Row(id='3811', ...)

In [41]:
#ATR related SL TP
dfpl = df[:]
from backtesting import Strategy
from backtesting import Backtest
class MyStrat(Strategy):
    initsize = 0.2
    mysize = initsize
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        slatr = 1.3*self.data.ATR[-1]
        TPSLRatio = 1.3
        #if(self.signal1>0 and len(self.trades)==0 and len(self.closed_trades)>0 and self.closed_trades[-1].pl < 0):
        #    self.mysize=self.mysize*2
        #elif len(self.closed_trades)>0 and self.closed_trades[-1].pl > 0:
        #    self.mysize=self.initsize

        if self.signal1==2 and len(self.trades)==0:   
            sl1 = self.data.Close[-1] - slatr
            tp1 = self.data.Close[-1] + slatr*TPSLRatio
            self.buy(sl=sl1, tp=tp1, size=self.mysize)
        
        elif self.signal1==1 and len(self.trades)==0:         
            sl1 = self.data.Close[-1] + slatr
            tp1 = self.data.Close[-1] - slatr*TPSLRatio
            self.sell(sl=sl1, tp=tp1, size=self.mysize)

bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.00)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:31: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21153.0
Duration                              21153.0
Exposure Time [%]                    9.771202
Equity Final [$]                    98.721034
Equity Peak [$]                     103.75347
Return [%]                          -1.278966
Buy & Hold Return [%]               -0.773838
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                   -5.843799
Avg. Drawdown [%]                   -0.399228
Max. Drawdown Duration                10243.0
Avg. Drawdown Duration             550.742857
# Trades                                362.0
Win Rate [%]                        45.303867
Best Trade [%]                        0.05287
Worst Trade [%]                     -0.042902
Avg. Trade [%]                    

In [42]:
bt.plot(show_legend=False)

Row(id='4597', ...)

In [43]:
#Trailing SL with ATR related distance
dfpl = df[:]
from backtesting import Strategy, Backtest
import numpy as np

class MyStrat(Strategy):
    
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        sltr = 1.5*self.data.ATR[-1]
        for trade in self.trades: 
            if trade.is_long: 
                trade.sl = max(trade.sl or -np.inf, self.data.Close[-1] - sltr)
                if self.signal1==1:
                    trade.close()
            else:
                trade.sl = min(trade.sl or np.inf, self.data.Close[-1] + sltr) 
                if self.signal1==2:
                    trade.close()
                    
        if self.signal1==2 and len(self.trades)==0:
            sl1 = self.data.Close[-1] - sltr
            self.buy(sl=sl1)
        elif self.signal1==1 and len(self.trades)==0:
            sl1 = self.data.Close[-1] + sltr
            self.sell(sl=sl1)


bt = Backtest(dfpl, MyStrat, cash=100, margin=1/50, commission=.000)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:33: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                   21153.0
Duration                              21153.0
Exposure Time [%]                   13.037723
Equity Final [$]                    96.897167
Equity Peak [$]                    120.361759
Return [%]                          -3.102833
Buy & Hold Return [%]               -0.773838
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -27.248553
Avg. Drawdown [%]                   -2.287369
Max. Drawdown Duration                14833.0
Avg. Drawdown Duration             951.727273
# Trades                                356.0
Win Rate [%]                        36.235955
Best Trade [%]                       0.141707
Worst Trade [%]                     -0.038349
Avg. Trade [%]                    

In [44]:
bt.plot()

Row(id='5383', ...)